In [251]:
from __future__ import division


# Library Packages
import regex as re
import itertools as it
import spacy
import numpy as np
import pandas as pd


# Settings
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
seed = 7
np.random.seed(seed)

import warnings

warnings.filterwarnings('ignore')


def front(self, n):
    return self.iloc[:, :n]


def back(self, n):
    return self.iloc[:, -n:]

from sklearn.preprocessing import StandardScaler
np.set_printoptions(threshold=np.nan)

from datetime import datetime
from dateutil.parser import parse
from nltk.sentiment.vader import SentimentIntensityAnalyzer as SIA
import re
from nltk.corpus import stopwords
from nltk.tokenize import wordpunct_tokenize
from sklearn.preprocessing import MinMaxScaler
from datetime import datetime, date
# Entity Extraction From Review
import itertools as it
import spacy


def Standardisation(df):
    listed = list(df)
    scaler = StandardScaler()
    scaled = scaler.fit_transform(df)
    df = pd.DataFrame(scaled)
    df.columns = listed
    return df



# Like normalization, standardization can be useful, and even required in some
# machine learning algorithms when your time series data has input values with differing scales.


from pandas_datareader.google.daily import GoogleDailyReader
from datetime import datetime, timedelta
import os

class FixedGoogleDailyReader(GoogleDailyReader):
    @property
    def url(self):
        return 'http://finance.google.com/finance/historical'


my_path = os.path.abspath(os.path.dirname('__file__'))
path = os.path.join(my_path, "../input_fields.csv")

input_fields = pd.read_csv(path).loc[:,:]

companies = input_fields["code_or_ticker"]

#tick  = [x for x in input_fields[input_fields["ticker"]!="PE"].ticker]

code  = [x for x in input_fields["code_or_ticker"]]

year = int(2007)
tick = code

import intrinio
intrinio.client.username = 'xxxxx'
intrinio.client.password = 'xxxxx'

for tic, cod in zip(tick, code):
    
#for tic, code in zip(["BKC"],["BKC"]):

    start = datetime(year, 1, 1)
    end = datetime.now()
    r = intrinio.prices(cod, start_date=str(year)+'-01-01')
    df_tick = r.rename( columns={'adj_volume': 'volume'})
    df_tick = df_tick.reset_index()
    df_tick = df_tick.rename( columns={'Volume': 'volume', 'Close': 'close', 'High': 'high', 'Low': 'low', 'Open': 'open', 'Date': 'date'})


    def dala(glassdoor ,tam):
        tak = len(glassdoor)
        glassdoor[tam] = glassdoor[tam].fillna(glassdoor[tam].mean())
        glassdoor["roll25"] = pd.rolling_mean(glassdoor[tam],int(tak*0.05)+3)
        glassdoor["roll100"] = pd.rolling_mean(glassdoor[tam],int(tak*0.2))
        glassdoor["roll250"] = pd.rolling_mean(glassdoor[tam],int(tak*0.5))

        glassdoor["roll100"] = glassdoor["roll100"].fillna(glassdoor["roll25"])
        glassdoor["roll250"] = glassdoor["roll250"].fillna(glassdoor["roll100"])
        glassdoor["roll250"] = glassdoor["roll250"].fillna(glassdoor["roll25"])

        glassdoor = glassdoor.sort_values("Review Date", ascending=False)

        glassdoor["special_25"] = pd.rolling_mean(glassdoor[tam],int(tak*0.05)+3)

        glassdoor["special_25"] = glassdoor["special_25"]*.80 + glassdoor[tam]*.10
        # Left 10% out here, that is okay I assume.

        glassdoor["roll100"] = glassdoor["roll100"].fillna(glassdoor["special_25"])
        glassdoor["roll25"] = glassdoor["roll25"].fillna(glassdoor["special_25"])
        glassdoor["roll250"] = glassdoor["roll250"].fillna(glassdoor["special_25"])

        glassdoor = glassdoor.sort_values("Review Date", ascending=True)

        glassdoor["Final_Rating"] = glassdoor["roll25"]*.60 + glassdoor["roll100"] *.30 + glassdoor["roll100"] *.10

        #multiplier = df_tick["close"].tail(1).values[0] / glassdoor["Final_Rating"].tail(1).values[0]

        #glassdoor["Final_Rating"] = glassdoor["Final_Rating"] * multiplier


        return glassdoor["Final_Rating"]
    #
    path = os.path.join(my_path, "../data/glassdoor/")

    glassdoor = pd.read_csv(path +cod +"_review.csv")

    # This is just the glassdoor processing step.
    
    glassdoor.loc[:,"Rating":"Senior Management"] = glassdoor.loc[:,"Rating":"Senior Management"].fillna(glassdoor.loc[:,"Rating":"Senior Management"].mean())

    glassdoor["Time Employeed"] = glassdoor["Time Employeed"].fillna(glassdoor["Time Employeed"].mode().values[0])
    glassdoor["Review Date"] = glassdoor["Review Date"].fillna(method="bfill")
    glassdoor["Review Date"] = glassdoor["Review Date"].fillna(method="ffill")
    glassdoor["Full-Time or Part-Time"] = glassdoor["Full-Time or Part-Time"].fillna(method="bfill")
    glassdoor["Full-Time or Part-Time"] = glassdoor["Full-Time or Part-Time"].fillna(method="ffill")
    
    #default_date = datetime.combine(date.today(), datetime.min.time()).replace(day=1)
    #try:
    #glassdoor['Review Date'] = glassdoor['Review Date'].apply(lambda x: parse(str(x),smart_defaults=default_date))
    
    glassdoor['Review Date'] = pd.to_datetime(glassdoor['Review Date'], infer_datetime_format=True, errors='coerce' )
    glassdoor = glassdoor[~glassdoor['Review Date'].isnull()]
    
    # Good
    # Bad
    # Great
    # Severe

    glassdoor["Pros"] = glassdoor["Pros"].apply(lambda x: re.sub('<br\s*?>', '. ', str(x)))
    glassdoor["Cons"] = glassdoor["Cons"].apply(lambda x: re.sub('<br\s*?>', '. ', str(x)))
    glassdoor["Advice to Management"] = glassdoor["Advice to Management"].fillna(value="").apply(
        lambda x: re.sub('<br\s*?>', '. ', str(x)))

    glassdoor["Location"] = glassdoor["Location"].fillna(method="bfill")
    glassdoor["Location"] = glassdoor["Location"].fillna(method="ffill")

    glassdoor["Location"] = glassdoor["Location"].apply(lambda x: str(x).split(",")[0])


    glassdoor = glassdoor.sort_values("Review Date", ascending=True)

    glassdoor_clean = glassdoor
    for tam in ["Rating", "Work Life Balance", "Culture Values", "Career Opportunities", "Comp Benefits",
                "Senior Management"]:
        glassdoor["Final_" + tam] = dala(glassdoor, tam)


    my_path = os.path.abspath(os.path.dirname('__file__'))
    path = os.path.join(my_path, "../data/yelp/"+cod+"/")

    path_out = os.path.join(my_path, "../data/ratings/")

    from os import listdir
    from os.path import isfile, join

    onlyfiles = [f for f in listdir(path) if isfile(join(path, f))]
    if '.DS_Store' in onlyfiles:
        onlyfiles.remove('.DS_Store')

###
    for file  in onlyfiles:

        yelp = pd.read_csv(path + file)

        yelp["date"] = yelp["date"].apply(lambda x: x[:10])
        yelp["date"] = yelp["date"].apply(lambda x: x[:-1] if x[-1]=="\\" else x )
        yelp["date"] = yelp["date"].apply(lambda x: x[:-2] if x[-1]=="n" else x )

        from datetime import datetime
        from dateutil.parser import parse

        yelp['date'] = yelp['date'].apply(lambda x: parse(x))


        yelp = yelp.sort_values("date", ascending=True)

        yelp["roll25"] = pd.rolling_mean(yelp["rating"],int(len(yelp)*.10))
        yelp["roll100"] = pd.rolling_mean(yelp["rating"],int(len(yelp)*.40))
        yelp["roll250"] = pd.rolling_mean(yelp["rating"],int(len(yelp)*.70))

        yelp["roll100"] = yelp["roll100"].fillna(yelp["roll25"])
        yelp["roll250"] = yelp["roll250"].fillna(yelp["roll100"])
        yelp["roll250"] = yelp["roll250"].fillna(yelp["roll25"])

        yelp = yelp.sort_values("date", ascending=False)

        yelp["special_25"] = pd.rolling_mean(yelp["rating"],int(len(yelp)*.10))

        yelp["special_25"] = yelp["special_25"]*.80 + yelp["rating"]*.25
        
        yelp["special_25"] = yelp["special_25"].fillna(method="ffill")
        # Left 10% out here, that is okay I assume.

        yelp["roll100"] = yelp["roll100"].fillna(yelp["special_25"])
        yelp["roll25"] = yelp["roll25"].fillna(yelp["special_25"])
        yelp["roll250"] = yelp["roll250"].fillna(yelp["special_25"])
        yelp["special_25"] = yelp["special_25"].shift(-1)
        
        yelp = yelp.sort_values("date", ascending=True)
        yelp["special_25"] = yelp["special_25"].fillna(method="bfill")

        yelp["Final_Rating"] = yelp["roll25"]*.40 + yelp["roll100"] *.40 + yelp["roll250"] *.20

        #multiplier = df_tick["close"].tail(1).values[0]/yelp["Final_Rating"].tail(1).values[0]

        #yelp["Final_Rating"] = yelp["Final_Rating"] * multiplier
        yelp = yelp[yelp["date"] > "2012-01-01"]

        yelp = yelp[yelp["date"] > "2012-01-01"]
        yelp.to_csv(path_out +file[:-4] + "_customer_ratings.csv")


    glassdoor = glassdoor[glassdoor["Review Date"]>"2012-01-01"]
    df_tick = df_tick[df_tick["date"]>"2012-01-01"]



    glassdoor_clean["manager"] = glassdoor_clean["Employee Title"].apply(lambda x:1 if "Manager" in str(x) else 0)

    

    glassdoor_m = glassdoor_clean[glassdoor_clean["manager"]==1]

    for tam in ["Rating","Work Life Balance","Culture Values","Career Opportunities","Comp Benefits","Senior Management"]:
        glassdoor_m["Final_"+tam] = dala(glassdoor_m,tam)


    glassdoor = glassdoor[glassdoor["Review Date"]>"2012-01-01"]
    glassdoor_m = glassdoor_m[glassdoor_m["Review Date"]>"2012-01-01"]


    # Date processing. ANd M
    glassdoor["Review Date"] = pd.to_datetime(glassdoor["Review Date"])
    glassdoor_m["Review Date"] = pd.to_datetime(glassdoor_m["Review Date"])
    df_tick["date"] = pd.to_datetime(df_tick["date"])

    kas = pd.DataFrame()
    beg = pd.Timestamp('2010-05-15')
    end = pd.Timestamp('2017-12-15')
    idx = pd.DatetimeIndex(start=beg, end=end, freq='D')

    kas["date"] = idx

    glassdoor_m = pd.merge(kas, glassdoor_m, left_on="date", right_on="Review Date", how="left")

    glassdoor_fake = pd.merge(kas, glassdoor, left_on="date", right_on="Review Date", how="left")


    glassdoor_m = pd.merge(glassdoor_fake, glassdoor_m,on="date",how="left")


    glassdoor_m = glassdoor_m[glassdoor_m["date"]>"2012-01-01"]

    glassdoor_m = glassdoor_m[glassdoor_m["date"]<=df_tick["date"].max()]

    glassdoor_m.reset_index(drop=True, inplace=True)

    glassdoor_m.fillna(method="ffill", inplace=True)

    glassdoor_m.fillna(method="bfill", inplace=True)


    glassdoor_m["trace_mse"] = ((((glassdoor_m["Final_Rating_y"]+ glassdoor_m["Final_Senior Management_y"]+glassdoor_m["Final_Work Life Balance_y"]+glassdoor_m["Final_Culture Values_y"]+glassdoor_m["Final_Career Opportunities_y"]+glassdoor_m["Final_Comp Benefits_y"])/6)+glassdoor_m["Final_Rating_x"])/2)

    glassdoor_m["trace_mwlb"] = (glassdoor_m["Final_Work Life Balance_x"]+glassdoor_m["Final_Work Life Balance_y"])/2

    glassdoor_m["trace_mcva"] = (glassdoor_m["Final_Culture Values_x"]+glassdoor_m["Final_Culture Values_y"])/2
    glassdoor_m["trace_mcop"] = (glassdoor_m["Final_Career Opportunities_x"]+glassdoor_m["Final_Career Opportunities_y"])/2
    glassdoor_m["trace_mcbe"] = (glassdoor_m["Final_Comp Benefits_x"]+glassdoor_m["Final_Comp Benefits_y"])/2
    glassdoor_m["trace_msma"] = (glassdoor_m["Final_Senior Management_x"]+glassdoor_m["Final_Senior Management_y"])/2




    df_tick = df_tick[df_tick["date"]>"2012-01-01"]


    glassdoor = glassdoor[glassdoor["Review Date"]<=df_tick["date"].max()]

    glassdoor.to_csv(path_out + cod +"_gdoor_employee_rate.csv")
    glassdoor_m.to_csv(path_out + cod +"_gdoor_mgmt_rate.csv")

    multiplier = (glassdoor_m["trace_mse"].tail(1)).values[0]/df_tick["close"].tail(1).values[0]

    df_tick["close"] = df_tick["close"] * multiplier


    df_tick.to_csv(path_out + cod +"_stock_rate.csv")
    print(cod)

FOGO
FRSH
GTIM
HABT
JACK
KONA
LOCO
LUB
MCD
MRT
NATH
NDLS
PBPB
PNRA
PZZA
RAVE
RRGB
RT
RUTH
SBUX
SHAK
SONC
THI
TXRH
WEN
WING
ZOES


In [250]:
cod

'FOGO'

In [249]:
yelp.head()

Link  \
0  https://www.yelp.com/biz/fogo-de-chao-brazilia...   
1  https://www.yelp.com/biz/fogo-de-chão-brazilia...   
2  https://www.yelp.com/biz/fogo-de-chão-brazilia...   
3  https://www.yelp.com/biz/fogo-de-chão-brazilia...   
4  https://www.yelp.com/biz/fogo-de-chão-brazilia...   

                                             address  \
0  [{'streetaddress': '600 E Pratt St', 'addressl...   
1  [{'streetaddress': '4300 Belt Line Rd', 'addre...   
2  [{'streetaddress': '3101 Piedmont Rd', 'addres...   
3  [{'streetaddress': '440 Bellevue Way NE', 'add...   
4  [{'streetaddress': '133 N La Cienega Blvd', 'a...   

                                              review  
0  {'ratingstars': '4.0', 'ratingcount': '685', '...  
1  {'ratingstars': '4.0', 'ratingcount': '586', '...  
2  {'ratingstars': '4.5', 'ratingcount': '854', '...  
3  {'ratingstars': '4.0', 'ratingcount': '250', '...  
4  {'ratingstars': '4.0', 'ratingcount': '3408', ...

In [146]:
glassdoor_clean

Login                                              Title  \
2866  already logged                       "Overall Happy with the Job"   
2865  already logged     "BK...a great job for managers to learn from."   
2864  already logged  "Burger King a nice place to work and have fun !"   
2863  already logged                           "Burger King Management"   
3254  already logged  "First job, poor wages, horribly inefficient c...   
2862  already logged                                 "Burger King Cook"   
2861  already logged                            "burger king does good"   
2859  already logged                                "Assistant Manager"   
2860  already logged  "Great place to work if you're not self suppor...   
3252  already logged                                        "I love it"   
3253  already logged                                   "Okay First Job"   
2858  already logged                               "good place to work"   
2857  already logged                                      "Burger King"   
2856  already logged                       "Not the best place to work"   
2855  already logged              "For my first job, it is unbeatable."   
2854  already logged                                      "Burger King"   
2853  already logged                              "Best place to learn"   
3251  already logged             "You're a dime a dozen at Burger King"   
3250  already logged                                           "its ok"   
2852  already logged                                          "Fun Job"   
3249  already logged  "OK place to work If you like the food industry."   
3248  already logged         "Not a bad experience... not super either"   
2851  already logged                                   "same ol things"   
3247  already logged                                      "burger king"   
3246  already logged                                      "Burger King"   
2850  already logged                                               "OK"   
2849  already logged                          "A good company overall!"   
3245  already logged                              "Chef doesn't cut it"   
2848  already logged  "Means to an end but move on if you are able t...   
2847  already logged                       "Restaurant General Manager"   
2846  already logged                           "A good first time job."   
3243  already logged                       "Great place to get started"   
3244  already logged  "B.K good for a first job, but that's the exte...   
2845  already logged                                "Sad Place to Work"   
2844  already logged                     "fast food what do you expect"   
3242  already logged                        "Good Entry Level position"   
2843  already logged                                        "It was ok"   
2842  already logged                                          "Fry dis"   
2840  already logged                              "Life at Burger king"   
2841  already logged                                 "Its work not fun"   
3241  already logged                             "Burger King Employee"   
2839  already logged                             "I loved my job there"   
3240  already logged  "IF YOU'RE LOOKING FOR AN OKAY WORK EXPERIENCE...   
3239  already logged                                  "employer review"   
3238  already logged                                                "."   
2838  already logged       "Lots of labor and a lot of hateful people."   
3237  already logged                               "Former Crew member"   
2837  already logged                                       "why i quit"   
3236  already logged                                        "Very nice"   
2836  already logged  "My overall experience with Burger King was gr...   
3235  already logged                                      "It was good"   
3233  already logged   "Loved my job...unfortunately it was eliminate."   
2834  already logged  "Was a great place

In [59]:
path = os.path.join(my_path, "../data/glassdoor/")
glassdoor = pd.read_csv(path +cod +"_review.csv")
glassdoor

Title  Rating  \
0                                  "History of Change"     5.0   
1                            "Burger King Crew Member"     4.0   
2                                  "Assistant Manager"     4.0   
3                               "I loved working here"     4.0   
4                                "Great Place to work"     4.0   
5                                               "Cook"     4.0   
6                                         "The review"     5.0   
7                                            "cashier"     4.0   
8                                            "Cashier"     4.0   
9                                        "Hardworking"     5.0   
10                              "Care free enviorment"     2.0   
11             "I was a very hard working crew member"     2.0   
12                                   "General manager"     2.0   
13   "My position is challenging at times, but over...     4.0   
14                                 "Assistant manager"     5.0   
15                    "hard worker and very motivated"     5.0   
16                                           "Cashier"     3.0   
17                                           "Cashier"     4.0   
18                                               "Ugh"     3.0   
19                                           "cashier"     2.0   
20             "What's really the price on hard work?"     4.0   
21                                           "BK crww"     3.0   
22                 "Good but everything kept breaking"     4.0   
23                         "Sadly More Cons Than Pros"     3.0   
24                              "Grossly Dissapointed"     2.0   
25                                 "Assistant Manager"     3.0   
26             "Good first time job for high schooler"     4.0   
27                           "I am a long time closer"     4.0   
28                                  "Not enough hours"     3.0   
29                            "Burger King employment"     4.0   
30                                           "Awesome"     5.0   
31                                   "Great Franchise"     5.0   
32                                           "cashier"     4.0   
33                                    "Good First Job"     4.0   
34                                "Loved working here"     5.0   
35                                              "Cook"     5.0   
36                                           "Wt....f"     2.0   
37                                  "Great Job, Team!"     5.0   
38                                          "Terrible"     1.0   
39     "Burger King: Like every other fast food chain"     4.0   
40                                   "Burger King Job"     3.0   
41        "Corporation is good, Franchise is terrible"     3.0   
42                                              "Ehhh"     2.0   
43                                    "Small potatoes"     3.0   
44                                              "Open"     4.0   
45                                   "High School Job"     3.0   
46             "Good job employ moral needs some work"     3.0   
47                             "Did not give me hours"     3.0   
48                                         "Chill job"     5.0   
49                                        "Terrible!!"     1.0   
50                   "Burger King was ok as part time"     4.0   
51                     "Good place to get experiences"     4.0   
52                                      "Opening cook"     4.0   
53   "Working at Burger was a great experience for ...     4.0   
54                       "Good for a first summer job"     3.0   
55                             "I love my job so much"     5.0   
56                                           "Cashier"     5.0   
57               "Great Part-Time option for Students"     4.0   
58                                           "Bus Boy"     5.0   
59                         "Depends who you work with"     3.0   
60                     

In [38]:
yelp["special_25"] = yelp["special_25"].fillna(yelp["special_25"].mean())

In [29]:
yelp["special_25"] = pd.rolling_mean(yelp["rating"],int(len(yelp)*.10)).fillna(method="ffill")

In [25]:
df_tick.head()

date  adj_close  adj_high  adj_low  adj_open    volume  close  \
0 2018-03-29      44.90     45.15   44.100     44.70  268427.0  44.90   
1 2018-03-28      44.50     45.00   43.695     43.80  298150.0  44.50   
2 2018-03-27      43.75     44.85   43.650     44.00  327645.0  43.75   
3 2018-03-26      43.90     44.00   42.360     43.75  414377.0  43.90   
4 2018-03-23      43.35     44.05   42.880     43.00  377148.0  43.35   

   ex_dividend   high     low   open  split_ratio    volume  
0          0.0  45.15  44.100  44.70          1.0  268427.0  
1          0.0  45.00  43.695  43.80          1.0  298150.0  
2          0.0  44.85  43.650  44.00          1.0  327645.0  
3          0.0  44.00  42.360  43.75          1.0  414377.0  
4          0.0  44.05  42.880  43.00          1.0  377148.0